## Loading packages

In [1]:
from genepy.utils import helper as h

# to comment in your case
from taigapy import TaigaClient
tc = TaigaClient()

from celligner import Celligner
import pandas as pd
# to comment in your case
from depmapomics import tracker as track
#autoreload
%load_ext autoreload
%autoreload 2
#output
from bokeh.plotting import output_notebook
output_notebook()

/home/jeremie/celligner/celligner/mnnpy/mnnpy/utils.py:14: NumbaWarning: 
Compilation is falling back to object mode WITH looplifting enabled because Function "l2_norm" failed type inference due to: No implementation of function Function(<function norm at 0x7fa25814ce18>) found for signature:
 
 >>> norm(x=array(float32, 2d, A), axis=Literal[int](1))
 
There are 2 candidate implementations:
  - Of which 2 did not match due to:
  Overload in function 'norm_impl': File: numba/np/linalg.py: Line 2352.
    With argument(s): '(x=array(float32, 2d, A), axis=int64)':
   Rejected as the implementation raised a specific error:
     TypeError: norm_impl() got an unexpected keyword argument 'x'
  raised from /home/jeremie/miniconda3/lib/python3.7/site-packages/numba/core/typing/templates.py:722

During: resolving callee type: Function(<function norm at 0x7fa25814ce18>)
During: typing of call at /home/jeremie/celligner/celligner/mnnpy/mnnpy/utils.py (16)


File "celligner/mnnpy/mnnpy/utils.py", li

Loading BokehJS ...

## Loading expression files

In [2]:
# load from taiga public (figshare link)
# load internal expression,
# latest version can be found at https://depmap.org/portal/download/
# can also be loaded like so pd.read_csv('gs://ccle_default_params/celligner_ex/CCLE_expression.csv.gz', index_col=0)
CCLE_expression = tc.get(name='internal-21q3-fe4c',
                         file='CCLE_expression_full')  


# load  TCGA expression
# this dataset was generated from  ,using this script: 
# caan be found here: pd.read_csv('gs://ccle_default_params/celligner_ex/TCGA_expression.csv.gz', index_col=0)
TCGA_expression = tc.get(name='celligner-input-9827',
                         file='tumor_expression')

No dataset version provided. Using version 16.
No dataset version provided. Using version 1.


In [3]:
# subset gene names to ensembl ids only
CCLE_expression = CCLE_expression[CCLE_expression.columns[:-92]]
CCLE_expression.columns = list(map(lambda x: x.split(
    ' (')[1][:-1] if ' (' in x else x, CCLE_expression.columns))

common = set(CCLE_expression.columns).intersection(
    set(TCGA_expression.columns))
CCLE_expression = CCLE_expression[list(common)]
TCGA_expression = TCGA_expression[list(common)]

## Managing annotations

In [4]:
# loading annotations
CCLE_annotation = track.getTracker() # the function uses pygsheets to load this: REFSHEET_URL=https://docs.google.com/spreadsheets/d/1Pgb5fIClGnErEqzxpU7qqX6ULpGTDjvzWwDN8XUJKIY
# Sheets.from_files(MY_ID, MYSTORAGE_ID).get(REFSHEET_URL).sheets[0].to_frame(index_col=0)
# you can also get it from pd.read_csv('gs://ccle_default_params/celligner_ex/CCLE_annotation.csv.gz', index_col=0)


# can be loaded from 
# pd.read_csv('gs://ccle_default_params/celligner_ex/TCGA_annotation.csv.gz', index_col=0)
TCGA_annotation = tc.get(name='celligner-input-9827',
                         file='tumor_annotations') # generated manually 

No dataset version provided. Using version 1.


In [5]:
# transforming annotations
CCLE_annotation = CCLE_annotation.drop_duplicates('arxspan_id').set_index("arxspan_id")
CCLE_annotation = CCLE_annotation.loc[CCLE_expression.index, ["origin", 'subtype']].rename(columns={"origin": "tissue_type", "subtype": 'disease_type'})
CCLE_annotation["cell_type"] = "cancer cell line"

TCGA_annotation = TCGA_annotation.set_index("sampleID").loc[TCGA_expression.index,["lineage",
"subtype"]].rename(columns={"lineage":"tissue_type", "subtype": 'disease_type'})
TCGA_annotation['cell_type'] = "tumor sample"

In [6]:
# some name are not consistent between the two datasets
rename = {np.nan: "unknown", "adrenal_cortex": "adrenal", "colorectal": "colon", 'thymus': 'thyroid',}
CCLE_annotation = CCLE_annotation.replace({"tissue_type": rename})
TCGA_annotation = TCGA_annotation.replace({"tissue_type": rename})

## Fitting celliner with the CCLE dataset 

In [ ]:
# fix seed

In [10]:
my_alligner = Celligner(make_plots=True)
my_alligner.fit(CCLE_expression, CCLE_annotation)

fetching gene names from biomart cache
using only usefull genes
looking at 1411 samples.
found 29593 common genes
creating a fit dataset..
reducing dimensionality...
clustering...
         Falling back to preprocessing with `sc.pp.pca` and default params.


doing differential expression analysis on the clusters
running differential expression on 38 clusters
running limmapy on the samples
you need to have R installed with the limma library installed
3.4.5
done


In [20]:
my_alligner.mnn_kwargs = {'k1': 5, 'k2': 50, "var_adj":False}

In [22]:
# running with regular mnn
my_alligner.method = "mnn"
_ = my_alligner.transform(TCGA_expression, TCGA_annotation)

looking at 12236 samples.
found 29593 common genes
creating a transform input..
reducing dimensionality...
clustering..
         Falling back to preprocessing with `sc.pp.pca` and default params.


doing differential expression analysis on the clusters..
running differential expression on 57 clusters
running limmapy on the samples
you need to have R installed with the limma library installed
3.4.5
there is 0.0 overlap between the fit and transform dataset in their most variable genes
doing cPCA..
transform
regressing out the cPCA components..
doing the MNN analysis using scanPy MNN...
Performing cosine normalization...
Starting MNN correct iteration. Reference batch: 0
Step 1 of 1: processing batch 1
  Looking for MNNs...
found 7864 mnns..
  Computing correction vectors...
  Applying correction...
MNN correction complete. Gathering output...
done
reducing dimensionality...
making plot...


In [24]:
my_alligner.fit_annotations

tissue_type          disease_type         cell_type
ACH-001113           lung                 NSCLC  cancer cell line
ACH-001289    soft_tissue                  ATRT  cancer cell line
ACH-001339           skin              melanoma  cancer cell line
ACH-001538      bile_duct    cholangiocarcinoma  cancer cell line
ACH-000242  urinary_tract     bladder_carcinoma  cancer cell line
...                   ...                   ...               ...
ACH-000750           skin              melanoma  cancer cell line
ACH-000285     lymphocyte  non_hodgkin_lymphoma  cancer cell line
ACH-001858      bile_duct    cholangiocarcinoma  cancer cell line
ACH-001997      bile_duct    cholangiocarcinoma  cancer cell line
ACH-000052           bone         Ewing_sarcoma  cancer cell line

[1411 rows x 3 columns]

In [26]:
TISSUE_COLOR

{'blood': '#1f77b4',
 'engineered_blood': '#1f77b4',
 'bone': '#aec7e8',
 'lymphocyte': '#17becf',
 'plasma_cell': '#9edae5',
 'central_nervous_system': '#ff7f0e',
 'engineered_central_nervous_system': '#ff7f0e',
 'peripheral_nervous_system': '#ffbb78',
 'nerve': '#dbdb8d',
 'eye': '#bcbd22',
 'liver': '#9467bd',
 'bile_duct': '#a55194',
 'pancreas': '#e377c2',
 'gastric': '#c49c94',
 'colon': '#8c564b',
 'engineered': '#bdbdbd',
 'fibroblast': '#969696',
 'skin': '#969696',
 'soft_tissue': '#cedb9c',
 'unknown': '#bdbdbd',
 'teratoma': '#252525',
 'germ_cell': '#c7c7c7',
 'embryo': '#7f7f7f',
 'lung': '#d62728',
 'engineered_lung': '#d62728',
 'upper_aerodigestive': '#ff9896',
 'nasopharynx': '#f7b6d2',
 'esophagus': '#e7969c',
 'ovary': '#2ca02c',
 'engineered_ovary': '#2ca02c',
 'uterus': '#98df8a',
 'cervix': '#5ab172',
 'prostate': '#637939',
 'engineered_prostate': '#637939',
 'thyroid': '#8c6d31',
 'endocrine': '#bd9e39',
 'pineal': '#e7ba52',
 'adrenal': '#8ca252',
 'kidney': '

In [25]:
from celligner.params import TISSUE_COLOR
my_alligner.plot(color_column="tissue_type", colortable=TISSUE_COLOR, rerun=False)

reducing dimensionality...
making plot...


In [16]:
my_alligner.pca_transform = my_alligner.pca_transform.fit(my_alligner.transform_input)

In [8]:
my_alligner.transform_input.shape

(12236, 29593)

In [12]:
# using the marioni mnn method
my_alligner.method = "mnn_marioni"
my_alligner.make_plots=False
_ = my_alligner.transform(_rerun=False)

KeyboardInterrupt: 

In [18]:
my_alligner.plot(color_column="tissue_type", colortable=TISSUE_COLOR)

reducing dimensionality...
making plot...


In [ ]:
my_alligner.plot()

In [ ]:
my_alligner.plot(color_column="tissue_type")

In [18]:
my_alligner.save('../temp/demo/')

## adding another dataset to celligner

In [13]:
my_alligner.mnn_kwargs = {'k1': 50, 'k2': 5}

In [7]:
# you can load the dataset from gcp: (you can do so by hand or by installing gsutil)
# (make sure you have the right folder and then do:
# ! gsutil cp gs://ccle_default_params/cellinger_ex/model.pkl ../temp/demo/
my_alligner = Celligner()
my_alligner.load('../temp/demo/')

fetching gene names from biomart cache
using only usefull genes


In [ ]:
CCLF = tc.get()

In [ ]:
# if you want to align to both CCLE and TCGA, you can ask celligner to consider the two (fit + _pre-transformed_ transform datasets) as a fit dataset by calling:
# my_alligner.putAllToFit()

# you can add your dataset as a dataset to be aligned to, by puting it in fit:
# my_alligner.addToFit(yourdataset).transform()
# /!\ need to already have a transform dataset (if you loaded the example model, this is TCGA)

# you can add your dataset as one to align, by putting it in transform:
# my_alligner.addToTransform(yourdataset)
# /!\ need to already have a fit dataset (if you loaded the example model, this is CCLE)

# if your dataset is small enough it might actually not work well to put it in transform it seems!
# if your dataset is small and similar enough, you can add the parameter dotransform=False (or dofit=False) so that it doesn't fully retransforms or refit but uses cached computation instead.

my_alligner.addToFit().transform()

In [ ]:
my_alligner.plot(color_column="tissue_type")